In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data

import torchvision

import numpy as np
import matplotlib.pyplot as plt
from sklearn.datasets import load_boston
from sklearn.model_selection import train_test_split

In [2]:
boston = load_boston(return_X_y=False)

X_train, X_test, y_train, y_test = train_test_split(boston.data, boston.target, test_size=50, random_state=42)

X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=40, random_state=42)

X_train = torch.FloatTensor(X_train)
y_train = torch.FloatTensor(y_train).view(-1,1)

X_train_mean = X_train.mean(0)
X_train_std = X_train.std(0)
X_train_norm = X_train.add(-1, X_train_mean) / X_train_std


y_train_mean = torch.mean(y_train)
y_train_std = torch.std(y_train)
y_train_norm = y_train.add(-1, y_train_mean) / y_train_std

X_val = torch.FloatTensor(X_val)
y_val = torch.FloatTensor(y_val).view(-1,1)

X_test = torch.FloatTensor(X_test)
y_test = torch.FloatTensor(y_test).view(-1,1)

train_data = torch.utils.data.TensorDataset(X_train_norm, y_train_norm)
train_loader = torch.utils.data.DataLoader(train_data, batch_size=32, num_workers=0)

val_data = torch.utils.data.TensorDataset(X_val, y_val)
val_loader = torch.utils.data.DataLoader(val_data, batch_size=40)

test_data = torch.utils.data.TensorDataset(X_test, y_test)
test_loader = torch.utils.data.DataLoader(test_data, batch_size=50)

In [3]:
if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

class Model(nn.Module):

    def __init__(self):
        super(Model, self).__init__()
        self.model = nn.Sequential(
                      nn.Linear(13, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50,1, bias=True)
                    ).to(device)


    def forward(self, x):
        x = x.view(x.size(0), -1)
        x = self.model(x)
        return x

In [4]:
class evaluation(object):
    def __init__(self, test_data, n_samples, X_mean=None, X_std=None, y_mean=None, y_std=None):
        self.test_data = test_data
        self.X_mean = X_mean
        self.X_std = X_std
        self.y_mean = y_mean
        self.y_std = y_std
        self.n = 0
        self.avg_prediction = 0.
        self.sum_pp = 0.
        self.sumsqr_pp = 0.
        self.preds = torch.zeros(len(test_data.dataset),n_samples)

    def fn(self, model):

        with torch.autograd.no_grad():
            self.n += 1
            for x, y in iter(self.test_data):
                x = x.view(x.size(0), -1)

                if (self.X_mean is not None) & (self.X_std is not None):
                    x = (x - self.X_mean).float() / self.X_std

                standard_pred = model(x)

                if (self.y_mean is not None) & (self.y_std is not None):
                    standard_pred = standard_pred * self.y_std + self.y_mean
                
                self.preds[:,self.n-1] = standard_pred.view(-1,)
                self.avg_prediction = self.avg_prediction * (self.n - 1.) / self.n + standard_pred.view(-1,1) / self.n
                self.sum_pp += standard_pred
                self.sumsqr_pp += standard_pred * standard_pred
                std_pred = torch.sqrt((self.sumsqr_pp - (self.sum_pp * self.sum_pp) / self.n) / (self.n - 1))



                norm = torch.distributions.normal.Normal(y, std_pred)
                test_ll = norm.log_prob(self.avg_prediction).mean()



                error = nn.MSELoss(size_average=True)
                rmse = error(self.avg_prediction, y) ** 0.5

                return rmse, test_ll, self.preds

In [5]:
def gelman_rubin(x, return_var=False):
    m, n = x.size()

    var_between = torch.sum((torch.mean(x, 1) - torch.mean(x)) ** 2) / (m - 1)
    x_bar = torch.mean(x, 1).view(-1,1)

    var_within = torch.sum((x - x_bar) ** 2) / (m * (n - 1))

    var = var_within * (n - 1) / n + var_between

    if return_var:
        return var

    V = var_within + var_between / n

    return torch.sqrt(V / var_within)

def ess(x):
    m, n = x.size()
    
    s_sq = gelman_rubin(x, return_var = True)
    
    neg_autocorr = False
    t = 1
    
    variogram = lambda t: (sum(sum((x[j][i] - x[j][i-t]) ** 2 for i in range(t,n)) for j in range(m)) / (m * (n - t)))
    
    rho = torch.ones(n)
    
    while not neg_autocorr and (t < n):
        rho[t] = 1. - variogram(t) / (2. * s_sq)
        
        if not t % 2:
            neg_autocorr = sum(rho[(t-1):(t+1)]) < 0
        t += 1
        
    return float(m * n)/ (1. + 2. * rho[1:t].sum())

## SGLD

In [9]:
import torch
import torchvision
import os

from torch import nn
import torch.nn.functional as F
import numpy as np

import sgld

import model



np.random.seed(42)
torch.manual_seed(42)



lambda_ = 1.
#lr = 8e-7
#lr = 6e-6
#3e-2
lr = 9e-7



batch_size = 32.
dataset_size= 456.

n_samples = 300
n_chains = 10




ll_sgld = np.zeros((n_chains, n_samples))
rmse_sgld = np.zeros((n_chains, n_samples))
predictions_sgld = np.zeros((n_chains,n_samples,50))




for i in range(n_chains):
    network = Model()
    criterion = nn.MSELoss(size_average=False)
    optim = sgld.optim.sgld(network, lr, lambda_, batch_size, dataset_size)
    evaluate = evaluation(test_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)
    
    t = 1
    n = 0
    for epoch in range(2500):

        running_loss = 0
        for x, y in iter(train_loader):
            x = x.view(x.size(0), -1)

            network.zero_grad()
            output = network(x)
            loss = 0.5 * criterion(output, y)
            loss.backward()
            optim.step()



            running_loss += loss * batch_size / dataset_size


            if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                rmse_sgld[i, n], ll_sgld[i, n], predictions[i,n,:] = evaluate.fn(network)
                n += 1

            t += 1.
        print("chain {:d} - epoch {:d} - loss: {:.4f}".format(i, epoch, running_loss))

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 0 - loss: 6.3264
chain 0 - epoch 1 - loss: 4.1935
chain 0 - epoch 2 - loss: 3.8235
chain 0 - epoch 3 - loss: 3.6636
chain 0 - epoch 4 - loss: 3.5449
chain 0 - epoch 5 - loss: 3.5056
chain 0 - epoch 6 - loss: 3.4377
chain 0 - epoch 7 - loss: 3.4081
chain 0 - epoch 8 - loss: 3.2851
chain 0 - epoch 9 - loss: 3.3196
chain 0 - epoch 10 - loss: 3.2176
chain 0 - epoch 11 - loss: 3.1439
chain 0 - epoch 12 - loss: 3.0621
chain 0 - epoch 13 - loss: 3.0509
chain 0 - epoch 14 - loss: 2.8940
chain 0 - epoch 15 - loss: 2.9185
chain 0 - epoch 16 - loss: 2.9440
chain 0 - epoch 17 - loss: 3.0174
chain 0 - epoch 18 - loss: 2.8337
chain 0 - epoch 19 - loss: 2.7829
chain 0 - epoch 20 - loss: 2.7995
chain 0 - epoch 21 - loss: 2.6099
chain 0 - epoch 22 - loss: 2.5872
chain 0 - epoch 23 - loss: 2.5282
chain 0 - epoch 24 - loss: 2.4774
chain 0 - epoch 25 - loss: 2.4207


/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 26 - loss: 2.3584
chain 0 - epoch 27 - loss: 2.3002
chain 0 - epoch 28 - loss: 2.3542
chain 0 - epoch 29 - loss: 2.3542
chain 0 - epoch 30 - loss: 2.2136
chain 0 - epoch 31 - loss: 2.1872
chain 0 - epoch 32 - loss: 2.2550
chain 0 - epoch 33 - loss: 2.1506
chain 0 - epoch 34 - loss: 2.1658
chain 0 - epoch 35 - loss: 2.0625
chain 0 - epoch 36 - loss: 2.1358
chain 0 - epoch 37 - loss: 2.0676
chain 0 - epoch 38 - loss: 1.9712
chain 0 - epoch 39 - loss: 2.0623
chain 0 - epoch 40 - loss: 1.9483
chain 0 - epoch 41 - loss: 1.9764
chain 0 - epoch 42 - loss: 1.9928
chain 0 - epoch 43 - loss: 1.9496
chain 0 - epoch 44 - loss: 2.0303
chain 0 - epoch 45 - loss: 1.9976
chain 0 - epoch 46 - loss: 1.9698
chain 0 - epoch 47 - loss: 1.9359
chain 0 - epoch 48 - loss: 1.9205
chain 0 - epoch 49 - loss: 2.0029
chain 0 - epoch 50 - loss: 1.9798
chain 0 - epoch 51 - loss: 1.9911
chain 0 - epoch 52 - loss: 1.9343
chain 0 - epoch 53 - loss: 1.8469
chain 0 - epoch 54 - loss: 1.8240
chain 0 - epoc

chain 0 - epoch 268 - loss: 1.0538
chain 0 - epoch 269 - loss: 0.8183
chain 0 - epoch 270 - loss: 0.8187
chain 0 - epoch 271 - loss: 0.7584
chain 0 - epoch 272 - loss: 0.6964
chain 0 - epoch 273 - loss: 0.8225
chain 0 - epoch 274 - loss: 0.7477
chain 0 - epoch 275 - loss: 0.9412
chain 0 - epoch 276 - loss: 1.6247
chain 0 - epoch 277 - loss: 1.0020
chain 0 - epoch 278 - loss: 0.7835
chain 0 - epoch 279 - loss: 0.8824
chain 0 - epoch 280 - loss: 0.8948
chain 0 - epoch 281 - loss: 0.7723
chain 0 - epoch 282 - loss: 0.8281
chain 0 - epoch 283 - loss: 0.7225
chain 0 - epoch 284 - loss: 0.7802
chain 0 - epoch 285 - loss: 0.7705
chain 0 - epoch 286 - loss: 0.7195
chain 0 - epoch 287 - loss: 0.7902
chain 0 - epoch 288 - loss: 1.1435
chain 0 - epoch 289 - loss: 0.9391
chain 0 - epoch 290 - loss: 0.8909
chain 0 - epoch 291 - loss: 0.7544
chain 0 - epoch 292 - loss: 0.7220
chain 0 - epoch 293 - loss: 0.9478
chain 0 - epoch 294 - loss: 0.8508
chain 0 - epoch 295 - loss: 0.7884
chain 0 - epoch 296 

...

chain 9 - epoch 1511 - loss: 0.3337
chain 9 - epoch 1512 - loss: 0.3406
chain 9 - epoch 1513 - loss: 0.3688
chain 9 - epoch 1514 - loss: 0.3742
chain 9 - epoch 1515 - loss: 0.4444
chain 9 - epoch 1516 - loss: 0.5432
chain 9 - epoch 1517 - loss: 0.4337
chain 9 - epoch 1518 - loss: 0.3699
chain 9 - epoch 1519 - loss: 0.3620
chain 9 - epoch 1520 - loss: 0.3606
chain 9 - epoch 1521 - loss: 0.3480
chain 9 - epoch 1522 - loss: 0.3633
chain 9 - epoch 1523 - loss: 0.3856
chain 9 - epoch 1524 - loss: 0.3992
chain 9 - epoch 1525 - loss: 0.4052
chain 9 - epoch 1526 - loss: 0.4139
chain 9 - epoch 1527 - loss: 0.3988
chain 9 - epoch 1528 - loss: 0.4227
chain 9 - epoch 1529 - loss: 0.3349
chain 9 - epoch 1530 - loss: 0.4082
chain 9 - epoch 1531 - loss: 0.4459
chain 9 - epoch 1532 - loss: 0.4501
chain 9 - epoch 1533 - loss: 0.4102
chain 9 - epoch 1534 - loss: 0.3402
chain 9 - epoch 1535 - loss: 0.3437
chain 9 - epoch 1536 - loss: 0.3826
chain 9 - epoch 1537 - loss: 0.3848
chain 9 - epoch 1538 - loss:

chain 9 - epoch 1741 - loss: 0.2626
chain 9 - epoch 1742 - loss: 0.2734
chain 9 - epoch 1743 - loss: 0.2691
chain 9 - epoch 1744 - loss: 0.2797
chain 9 - epoch 1745 - loss: 0.2685
chain 9 - epoch 1746 - loss: 0.2710
chain 9 - epoch 1747 - loss: 0.2728
chain 9 - epoch 1748 - loss: 0.2616
chain 9 - epoch 1749 - loss: 0.2502
chain 9 - epoch 1750 - loss: 0.2651
chain 9 - epoch 1751 - loss: 0.2814
chain 9 - epoch 1752 - loss: 0.2724
chain 9 - epoch 1753 - loss: 0.2809
chain 9 - epoch 1754 - loss: 0.2704
chain 9 - epoch 1755 - loss: 0.2752
chain 9 - epoch 1756 - loss: 0.2719
chain 9 - epoch 1757 - loss: 0.2660
chain 9 - epoch 1758 - loss: 0.2689
chain 9 - epoch 1759 - loss: 0.2713
chain 9 - epoch 1760 - loss: 0.2622
chain 9 - epoch 1761 - loss: 0.2723
chain 9 - epoch 1762 - loss: 0.2719
chain 9 - epoch 1763 - loss: 0.2652
chain 9 - epoch 1764 - loss: 0.2641
chain 9 - epoch 1765 - loss: 0.2744
chain 9 - epoch 1766 - loss: 0.2661
chain 9 - epoch 1767 - loss: 0.2592
chain 9 - epoch 1768 - loss:

chain 9 - epoch 1971 - loss: 0.2557
chain 9 - epoch 1972 - loss: 0.2724
chain 9 - epoch 1973 - loss: 0.2649
chain 9 - epoch 1974 - loss: 0.2613
chain 9 - epoch 1975 - loss: 0.2497
chain 9 - epoch 1976 - loss: 0.2453
chain 9 - epoch 1977 - loss: 0.2486
chain 9 - epoch 1978 - loss: 0.2557
chain 9 - epoch 1979 - loss: 0.2503
chain 9 - epoch 1980 - loss: 0.2646
chain 9 - epoch 1981 - loss: 0.2635
chain 9 - epoch 1982 - loss: 0.2578
chain 9 - epoch 1983 - loss: 0.2543
chain 9 - epoch 1984 - loss: 0.2735
chain 9 - epoch 1985 - loss: 0.2471
chain 9 - epoch 1986 - loss: 0.2542
chain 9 - epoch 1987 - loss: 0.2619
chain 9 - epoch 1988 - loss: 0.2911
chain 9 - epoch 1989 - loss: 0.2674
chain 9 - epoch 1990 - loss: 0.2733
chain 9 - epoch 1991 - loss: 0.2672
chain 9 - epoch 1992 - loss: 0.2738
chain 9 - epoch 1993 - loss: 0.2773
chain 9 - epoch 1994 - loss: 0.2764
chain 9 - epoch 1995 - loss: 0.2832
chain 9 - epoch 1996 - loss: 0.2794
chain 9 - epoch 1997 - loss: 0.2891
chain 9 - epoch 1998 - loss:

chain 9 - epoch 2200 - loss: 0.2806
chain 9 - epoch 2201 - loss: 0.2671
chain 9 - epoch 2202 - loss: 0.2614
chain 9 - epoch 2203 - loss: 0.2775
chain 9 - epoch 2204 - loss: 0.2741
chain 9 - epoch 2205 - loss: 0.2879
chain 9 - epoch 2206 - loss: 0.2747
chain 9 - epoch 2207 - loss: 0.2684
chain 9 - epoch 2208 - loss: 0.2619
chain 9 - epoch 2209 - loss: 0.2582
chain 9 - epoch 2210 - loss: 0.2491
chain 9 - epoch 2211 - loss: 0.2560
chain 9 - epoch 2212 - loss: 0.2541
chain 9 - epoch 2213 - loss: 0.2469
chain 9 - epoch 2214 - loss: 0.2396
chain 9 - epoch 2215 - loss: 0.2450
chain 9 - epoch 2216 - loss: 0.2530
chain 9 - epoch 2217 - loss: 0.2473
chain 9 - epoch 2218 - loss: 0.2556
chain 9 - epoch 2219 - loss: 0.2661
chain 9 - epoch 2220 - loss: 0.2549
chain 9 - epoch 2221 - loss: 0.2626
chain 9 - epoch 2222 - loss: 0.2611
chain 9 - epoch 2223 - loss: 0.2764
chain 9 - epoch 2224 - loss: 0.2644
chain 9 - epoch 2225 - loss: 0.2675
chain 9 - epoch 2226 - loss: 0.2802
chain 9 - epoch 2227 - loss:

chain 9 - epoch 2429 - loss: 0.2262
chain 9 - epoch 2430 - loss: 0.2276
chain 9 - epoch 2431 - loss: 0.2302
chain 9 - epoch 2432 - loss: 0.2420
chain 9 - epoch 2433 - loss: 0.2329
chain 9 - epoch 2434 - loss: 0.2394
chain 9 - epoch 2435 - loss: 0.2403
chain 9 - epoch 2436 - loss: 0.2400
chain 9 - epoch 2437 - loss: 0.2269
chain 9 - epoch 2438 - loss: 0.2252
chain 9 - epoch 2439 - loss: 0.2306
chain 9 - epoch 2440 - loss: 0.2303
chain 9 - epoch 2441 - loss: 0.2331
chain 9 - epoch 2442 - loss: 0.2273
chain 9 - epoch 2443 - loss: 0.2308
chain 9 - epoch 2444 - loss: 0.2316
chain 9 - epoch 2445 - loss: 0.2387
chain 9 - epoch 2446 - loss: 0.2326
chain 9 - epoch 2447 - loss: 0.2371
chain 9 - epoch 2448 - loss: 0.2400
chain 9 - epoch 2449 - loss: 0.2354
chain 9 - epoch 2450 - loss: 0.2416
chain 9 - epoch 2451 - loss: 0.2414
chain 9 - epoch 2452 - loss: 0.2401
chain 9 - epoch 2453 - loss: 0.2376
chain 9 - epoch 2454 - loss: 0.2434
chain 9 - epoch 2455 - loss: 0.2533
chain 9 - epoch 2456 - loss:

In [ ]:
np.save(ll_sgld_boston, ll_sgld)
np.save(rmse_sgld_boston, rmse_sgld)
np.save(predictions_sgld_boston, predictions)

In [33]:
gelman_rubin(predictions)

tensor(1.0322)

In [ ]:
ess(predictions)

### avg. Test log-likelihood

In [10]:
# Compute avg- test log-likelihood and std. error 
ll_meanSGLD = np.mean(ll_sgld[:,-1])
ll_stdSGLD = np.std(ll_sgld[:,-1])
print(ll_meanSGLD, ll_stdSGLD)

-2.4959707021713258 0.1586524247056256


### avg. Test RMSE

In [23]:
rmse_meanSGLD = np.mean(rmse_sgld[:,-1])
rmse_stdSGLD = np.std(rmse_sgld[:,-1])
print(rmse_meanSGLD, rmse_stdSGLD)

2.880292510986328 0.2755296520698714


## pSGLD

In [11]:
import torch
import torchvision
import os

from itertools import chain
from torch import nn
from torchvision import transforms
import torch.nn.functional as F
import numpy as np

import psgld 

import model




np.random.seed(42)
torch.manual_seed(42)



lambda_ = 1.
#lr =7e-3
#lr = 1e-3
lr = 7e-3
alpha = 0.99


batch_size = 32
dataset_size= 456

n_chains = 10
n_samples = 300





ll_psgld = np.zeros((n_chains, n_samples))
rmse_psgld = np.zeros((n_chains, n_samples))
predictions_psgld = np.zeros((n_chains,n_samples,50))

for i in range(n_chains):
    network = Model()
    criterion = nn.MSELoss(size_average=False)
    optim = psgld.optim.psgld(network, lr, alpha, lambda_, batch_size, dataset_size)
    evaluate = evaluation(test_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)
    
    t = 1
    n = 0
    for epoch in range(2500):

        running_loss = 0
        for x, y in iter(train_loader):
            x = x.view(x.size(0), -1)

            network.zero_grad()
            output = network(x)
            loss = 0.5 * criterion(output, y)
            loss.backward()
            optim.step()

            running_loss += loss * batch_size / dataset_size


            if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                rmse_psgld[i, n], ll_psgld[i, n], predictions_psgld[i,n,:] = evaluate.fn(network)
                n += 1

            t += 1.
        print("chain {:d} - epoch {:d} - loss: {:.4f}".format(i, epoch, running_loss))

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 0 - loss: 29.0679
chain 0 - epoch 1 - loss: 4.3019
chain 0 - epoch 2 - loss: 3.7541
chain 0 - epoch 3 - loss: 3.2758
chain 0 - epoch 4 - loss: 2.9513
chain 0 - epoch 5 - loss: 2.7171
chain 0 - epoch 6 - loss: 2.6468
chain 0 - epoch 7 - loss: 2.4859
chain 0 - epoch 8 - loss: 2.4350
chain 0 - epoch 9 - loss: 2.3759
chain 0 - epoch 10 - loss: 2.1892
chain 0 - epoch 11 - loss: 2.1971
chain 0 - epoch 12 - loss: 2.0921
chain 0 - epoch 13 - loss: 2.0961
chain 0 - epoch 14 - loss: 2.0451
chain 0 - epoch 15 - loss: 1.9910
chain 0 - epoch 16 - loss: 1.8705
chain 0 - epoch 17 - loss: 2.2167
chain 0 - epoch 18 - loss: 1.8449
chain 0 - epoch 19 - loss: 2.4024
chain 0 - epoch 20 - loss: 1.6997
chain 0 - epoch 21 - loss: 1.6936
chain 0 - epoch 22 - loss: 1.6696
chain 0 - epoch 23 - loss: 1.7052


/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 24 - loss: 2.0435
chain 0 - epoch 25 - loss: 1.9818
chain 0 - epoch 26 - loss: 1.5598
chain 0 - epoch 27 - loss: 1.7289
chain 0 - epoch 28 - loss: 1.4490
chain 0 - epoch 29 - loss: 1.9160
chain 0 - epoch 30 - loss: 1.7074
chain 0 - epoch 31 - loss: 1.9926
chain 0 - epoch 32 - loss: 1.5060
chain 0 - epoch 33 - loss: 1.5241
chain 0 - epoch 34 - loss: 1.9589
chain 0 - epoch 35 - loss: 2.1172
chain 0 - epoch 36 - loss: 1.5627
chain 0 - epoch 37 - loss: 1.6080
chain 0 - epoch 38 - loss: 1.4444
chain 0 - epoch 39 - loss: 1.7234
chain 0 - epoch 40 - loss: 1.4064
chain 0 - epoch 41 - loss: 1.5719
chain 0 - epoch 42 - loss: 1.6462
chain 0 - epoch 43 - loss: 1.4766
chain 0 - epoch 44 - loss: 1.5667
chain 0 - epoch 45 - loss: 1.3885
chain 0 - epoch 46 - loss: 1.5541
chain 0 - epoch 47 - loss: 1.4181
chain 0 - epoch 48 - loss: 1.5623
chain 0 - epoch 49 - loss: 1.4416
chain 0 - epoch 50 - loss: 1.3378
chain 0 - epoch 51 - loss: 1.4445
chain 0 - epoch 52 - loss: 1.6810
chain 0 - epoc

chain 0 - epoch 264 - loss: 0.8680
chain 0 - epoch 265 - loss: 1.0416
chain 0 - epoch 266 - loss: 0.7672
chain 0 - epoch 267 - loss: 1.1582
chain 0 - epoch 268 - loss: 1.7740
chain 0 - epoch 269 - loss: 0.9758
chain 0 - epoch 270 - loss: 0.8536
chain 0 - epoch 271 - loss: 1.0522
chain 0 - epoch 272 - loss: 1.2914
chain 0 - epoch 273 - loss: 1.3428
chain 0 - epoch 274 - loss: 1.0275
chain 0 - epoch 275 - loss: 1.0479
chain 0 - epoch 276 - loss: 1.0327
chain 0 - epoch 277 - loss: 0.9455
chain 0 - epoch 278 - loss: 1.3645
chain 0 - epoch 279 - loss: 0.8868
chain 0 - epoch 280 - loss: 1.1641
chain 0 - epoch 281 - loss: 1.3944
chain 0 - epoch 282 - loss: 1.2626
chain 0 - epoch 283 - loss: 0.8220
chain 0 - epoch 284 - loss: 1.3989
chain 0 - epoch 285 - loss: 1.5066
chain 0 - epoch 286 - loss: 1.0633
chain 0 - epoch 287 - loss: 0.8972
chain 0 - epoch 288 - loss: 0.7786
chain 0 - epoch 289 - loss: 0.8606
chain 0 - epoch 290 - loss: 1.3592
chain 0 - epoch 291 - loss: 1.6204
chain 0 - epoch 292 

...

chain 9 - epoch 1502 - loss: 1.5543
chain 9 - epoch 1503 - loss: 1.6576
chain 9 - epoch 1504 - loss: 1.3712
chain 9 - epoch 1505 - loss: 0.8295
chain 9 - epoch 1506 - loss: 0.9797
chain 9 - epoch 1507 - loss: 1.1918
chain 9 - epoch 1508 - loss: 1.6052
chain 9 - epoch 1509 - loss: 0.6890
chain 9 - epoch 1510 - loss: 0.9446
chain 9 - epoch 1511 - loss: 0.7561
chain 9 - epoch 1512 - loss: 1.1147
chain 9 - epoch 1513 - loss: 1.3226
chain 9 - epoch 1514 - loss: 1.3640
chain 9 - epoch 1515 - loss: 0.7794
chain 9 - epoch 1516 - loss: 1.6661
chain 9 - epoch 1517 - loss: 1.1815
chain 9 - epoch 1518 - loss: 1.3815
chain 9 - epoch 1519 - loss: 1.2842
chain 9 - epoch 1520 - loss: 0.8207
chain 9 - epoch 1521 - loss: 1.6063
chain 9 - epoch 1522 - loss: 1.1338
chain 9 - epoch 1523 - loss: 0.9315
chain 9 - epoch 1524 - loss: 1.5900
chain 9 - epoch 1525 - loss: 1.5448
chain 9 - epoch 1526 - loss: 0.9900
chain 9 - epoch 1527 - loss: 1.0807
chain 9 - epoch 1528 - loss: 0.7733
chain 9 - epoch 1529 - loss:

chain 9 - epoch 1730 - loss: 1.0782
chain 9 - epoch 1731 - loss: 0.9654
chain 9 - epoch 1732 - loss: 1.5916
chain 9 - epoch 1733 - loss: 1.6378
chain 9 - epoch 1734 - loss: 1.0966
chain 9 - epoch 1735 - loss: 1.5019
chain 9 - epoch 1736 - loss: 1.3004
chain 9 - epoch 1737 - loss: 0.8571
chain 9 - epoch 1738 - loss: 0.9192
chain 9 - epoch 1739 - loss: 1.2697
chain 9 - epoch 1740 - loss: 0.8586
chain 9 - epoch 1741 - loss: 1.0086
chain 9 - epoch 1742 - loss: 0.8036
chain 9 - epoch 1743 - loss: 0.7769
chain 9 - epoch 1744 - loss: 1.7631
chain 9 - epoch 1745 - loss: 1.6287
chain 9 - epoch 1746 - loss: 1.4766
chain 9 - epoch 1747 - loss: 0.9806
chain 9 - epoch 1748 - loss: 0.8948
chain 9 - epoch 1749 - loss: 1.6257
chain 9 - epoch 1750 - loss: 0.9616
chain 9 - epoch 1751 - loss: 1.0688
chain 9 - epoch 1752 - loss: 1.6469
chain 9 - epoch 1753 - loss: 1.5922
chain 9 - epoch 1754 - loss: 1.0368
chain 9 - epoch 1755 - loss: 0.7757
chain 9 - epoch 1756 - loss: 0.8559
chain 9 - epoch 1757 - loss:

chain 9 - epoch 1959 - loss: 0.8875
chain 9 - epoch 1960 - loss: 1.7040
chain 9 - epoch 1961 - loss: 1.1721
chain 9 - epoch 1962 - loss: 1.1009
chain 9 - epoch 1963 - loss: 1.3484
chain 9 - epoch 1964 - loss: 2.1689
chain 9 - epoch 1965 - loss: 1.2605
chain 9 - epoch 1966 - loss: 0.7068
chain 9 - epoch 1967 - loss: 1.3202
chain 9 - epoch 1968 - loss: 1.3099
chain 9 - epoch 1969 - loss: 0.9788
chain 9 - epoch 1970 - loss: 1.6982
chain 9 - epoch 1971 - loss: 1.7707
chain 9 - epoch 1972 - loss: 0.6874
chain 9 - epoch 1973 - loss: 0.6666
chain 9 - epoch 1974 - loss: 1.8792
chain 9 - epoch 1975 - loss: 1.7012
chain 9 - epoch 1976 - loss: 1.3329
chain 9 - epoch 1977 - loss: 0.8915
chain 9 - epoch 1978 - loss: 1.2893
chain 9 - epoch 1979 - loss: 0.7692
chain 9 - epoch 1980 - loss: 0.8034
chain 9 - epoch 1981 - loss: 1.4340
chain 9 - epoch 1982 - loss: 1.4183
chain 9 - epoch 1983 - loss: 0.9744
chain 9 - epoch 1984 - loss: 1.3588
chain 9 - epoch 1985 - loss: 1.8190
chain 9 - epoch 1986 - loss:

chain 9 - epoch 2190 - loss: 0.9960
chain 9 - epoch 2191 - loss: 0.8757
chain 9 - epoch 2192 - loss: 1.3926
chain 9 - epoch 2193 - loss: 1.8378
chain 9 - epoch 2194 - loss: 0.9323
chain 9 - epoch 2195 - loss: 1.0867
chain 9 - epoch 2196 - loss: 0.9134
chain 9 - epoch 2197 - loss: 1.2579
chain 9 - epoch 2198 - loss: 1.6077
chain 9 - epoch 2199 - loss: 1.5208
chain 9 - epoch 2200 - loss: 1.5373
chain 9 - epoch 2201 - loss: 1.0392
chain 9 - epoch 2202 - loss: 1.3599
chain 9 - epoch 2203 - loss: 1.1284
chain 9 - epoch 2204 - loss: 1.4874
chain 9 - epoch 2205 - loss: 0.9093
chain 9 - epoch 2206 - loss: 0.8823
chain 9 - epoch 2207 - loss: 0.7608
chain 9 - epoch 2208 - loss: 1.3626
chain 9 - epoch 2209 - loss: 2.1197
chain 9 - epoch 2210 - loss: 1.4497
chain 9 - epoch 2211 - loss: 0.7111
chain 9 - epoch 2212 - loss: 0.9112
chain 9 - epoch 2213 - loss: 1.2275
chain 9 - epoch 2214 - loss: 2.2823
chain 9 - epoch 2215 - loss: 0.8919
chain 9 - epoch 2216 - loss: 1.3848
chain 9 - epoch 2217 - loss:

chain 9 - epoch 2418 - loss: 0.9767
chain 9 - epoch 2419 - loss: 1.6242
chain 9 - epoch 2420 - loss: 1.3577
chain 9 - epoch 2421 - loss: 1.1102
chain 9 - epoch 2422 - loss: 0.7365
chain 9 - epoch 2423 - loss: 1.0405
chain 9 - epoch 2424 - loss: 1.9496
chain 9 - epoch 2425 - loss: 1.0468
chain 9 - epoch 2426 - loss: 0.7354
chain 9 - epoch 2427 - loss: 0.7109
chain 9 - epoch 2428 - loss: 1.1707
chain 9 - epoch 2429 - loss: 1.5199
chain 9 - epoch 2430 - loss: 1.1616
chain 9 - epoch 2431 - loss: 1.1864
chain 9 - epoch 2432 - loss: 0.7621
chain 9 - epoch 2433 - loss: 1.0033
chain 9 - epoch 2434 - loss: 1.7035
chain 9 - epoch 2435 - loss: 1.2165
chain 9 - epoch 2436 - loss: 0.9529
chain 9 - epoch 2437 - loss: 1.4339
chain 9 - epoch 2438 - loss: 1.5219
chain 9 - epoch 2439 - loss: 1.0424
chain 9 - epoch 2440 - loss: 1.1934
chain 9 - epoch 2441 - loss: 1.7366
chain 9 - epoch 2442 - loss: 1.2555
chain 9 - epoch 2443 - loss: 1.3393
chain 9 - epoch 2444 - loss: 1.4513
chain 9 - epoch 2445 - loss:

In [ ]:
np.save(ll_psgld_boston, ll_psgld)
np.save(rmse_psgld_boston, rmse_psgld)
np.save(predictions_psgld_boston, predictions)

### avg. Test log-likelihood

In [12]:
ll_mean = np.mean(ll_psgld[:,-1])
ll_std = np.std(ll_psgld[:,-1])
print(ll_mean, ll_std)

-2.1635692358016967 0.051988003770953965


### avg. Test RMSE

In [15]:
rmse_mean = np.mean(rmse_psgld[:,-1])
rmse_std = np.std(rmse_psgld[:,-1])
print(rmse_mean, rmse_std)

2.472678303718567 0.13704393205997403


## K-SGFS

In [11]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np

import ksgfs



np.random.seed(42)
torch.manual_seed(42)
    
lr = 2e-2
l2 = 1e-3
lambda_ = 1.
eta = 1.
v = 0


batch_size = 32
dataset_size=456


n_chains = 10
n_samples = 300

ll_ksgfs = np.zeros((n_chains, n_samples))
rmse_ksgfs = np.zeros((n_chains, n_samples))


losses_ksgfs = []

for i in range(n_chains):
    network = Model()
    criterion = nn.MSELoss(size_average=False)

    optim = ksgfs.optim.KSGFS(network, criterion, batch_size, dataset_size, eta=eta, v=v, lambda_=lambda_, epsilon=lr, l2=l2, invert_every=1)
    evaluate = evaluation(test_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)
    t = 1
    n = 0
    for epoch in range(2500):

        running_loss = 0
        for x, y in iter(train_loader):
            x = x.view(x.size(0), -1)

            optim.update_curvature(x)

            network.zero_grad()
            output = network(x)
            loss = 0.5 * criterion(output, y)
            loss.backward()
            optim.step()

            running_loss += loss * batch_size / dataset_size

            if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                rmse, ll, predictions = evaluate.fn(network)

                ll_ksgfs[i, n] = ll
                rmse_ksgfs[i, n] = rmse

                n += 1

            t += 1.
        print("chain {:d} - epoch {:d} - loss: {:.4f}".format(i, epoch, running_loss))

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 0 - loss: 13.8378
chain 0 - epoch 1 - loss: 6.4616
chain 0 - epoch 2 - loss: 5.3819
chain 0 - epoch 3 - loss: 5.9367
chain 0 - epoch 4 - loss: 6.3384
chain 0 - epoch 5 - loss: 5.9117
chain 0 - epoch 6 - loss: 4.6962
chain 0 - epoch 7 - loss: 4.5484
chain 0 - epoch 8 - loss: 6.4301
chain 0 - epoch 9 - loss: 3.6698
chain 0 - epoch 10 - loss: 4.1045
chain 0 - epoch 11 - loss: 5.3946
chain 0 - epoch 12 - loss: 4.5625
chain 0 - epoch 13 - loss: 3.4463
chain 0 - epoch 14 - loss: 5.1890
chain 0 - epoch 15 - loss: 4.4073
chain 0 - epoch 16 - loss: 2.7949
chain 0 - epoch 17 - loss: 4.5077
chain 0 - epoch 18 - loss: 4.9323
chain 0 - epoch 19 - loss: 5.8326


/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 20 - loss: 4.1036
chain 0 - epoch 21 - loss: 2.6556
chain 0 - epoch 22 - loss: 5.2538
chain 0 - epoch 23 - loss: 2.2539
chain 0 - epoch 24 - loss: 2.7115
chain 0 - epoch 25 - loss: 2.1617
chain 0 - epoch 26 - loss: 4.2656
chain 0 - epoch 27 - loss: 5.3570
chain 0 - epoch 28 - loss: 2.4136
chain 0 - epoch 29 - loss: 5.1715
chain 0 - epoch 30 - loss: 2.1805
chain 0 - epoch 31 - loss: 2.6113
chain 0 - epoch 32 - loss: 1.6301
chain 0 - epoch 33 - loss: 8.2088
chain 0 - epoch 34 - loss: 3.2163
chain 0 - epoch 35 - loss: 3.3660
chain 0 - epoch 36 - loss: 3.1796
chain 0 - epoch 37 - loss: 3.1817
chain 0 - epoch 38 - loss: 2.6687
chain 0 - epoch 39 - loss: 3.7177
chain 0 - epoch 40 - loss: 1.7988
chain 0 - epoch 41 - loss: 2.1138
chain 0 - epoch 42 - loss: 1.7190
chain 0 - epoch 43 - loss: 4.3054
chain 0 - epoch 44 - loss: 4.6217
chain 0 - epoch 45 - loss: 2.9823
chain 0 - epoch 46 - loss: 2.0770
chain 0 - epoch 47 - loss: 2.6787
chain 0 - epoch 48 - loss: 3.8706
chain 0 - epoc

chain 0 - epoch 258 - loss: 2.9869
chain 0 - epoch 259 - loss: 2.5830
chain 0 - epoch 260 - loss: 2.9549
chain 0 - epoch 261 - loss: 2.8001
chain 0 - epoch 262 - loss: 2.8209
chain 0 - epoch 263 - loss: 3.1308
chain 0 - epoch 264 - loss: 2.6102
chain 0 - epoch 265 - loss: 2.5683
chain 0 - epoch 266 - loss: 2.4013
chain 0 - epoch 267 - loss: 2.3163
chain 0 - epoch 268 - loss: 5.6276
chain 0 - epoch 269 - loss: 2.8151
chain 0 - epoch 270 - loss: 3.3191
chain 0 - epoch 271 - loss: 2.5205
chain 0 - epoch 272 - loss: 4.7112
chain 0 - epoch 273 - loss: 2.9923
chain 0 - epoch 274 - loss: 2.8201
chain 0 - epoch 275 - loss: 3.4136
chain 0 - epoch 276 - loss: 4.8255
chain 0 - epoch 277 - loss: 2.6128
chain 0 - epoch 278 - loss: 2.6523
chain 0 - epoch 279 - loss: 2.3643
chain 0 - epoch 280 - loss: 2.1671
chain 0 - epoch 281 - loss: 3.1261
chain 0 - epoch 282 - loss: 2.3296
chain 0 - epoch 283 - loss: 2.5097
chain 0 - epoch 284 - loss: 3.3298
chain 0 - epoch 285 - loss: 3.2263
chain 0 - epoch 286 

...

chain 9 - epoch 1358 - loss: 2.5627
chain 9 - epoch 1359 - loss: 3.5661
chain 9 - epoch 1360 - loss: 2.3992
chain 9 - epoch 1361 - loss: 2.4736
chain 9 - epoch 1362 - loss: 2.0774
chain 9 - epoch 1363 - loss: 4.6697
chain 9 - epoch 1364 - loss: 2.6658
chain 9 - epoch 1365 - loss: 2.5730
chain 9 - epoch 1366 - loss: 2.1275
chain 9 - epoch 1367 - loss: 3.2718
chain 9 - epoch 1368 - loss: 2.1374
chain 9 - epoch 1369 - loss: 2.7632
chain 9 - epoch 1370 - loss: 2.1330
chain 9 - epoch 1371 - loss: 1.9493
chain 9 - epoch 1372 - loss: 2.2466
chain 9 - epoch 1373 - loss: 1.7626
chain 9 - epoch 1374 - loss: 1.7380
chain 9 - epoch 1375 - loss: 1.9023
chain 9 - epoch 1376 - loss: 3.4552
chain 9 - epoch 1377 - loss: 4.4391
chain 9 - epoch 1378 - loss: 1.8917
chain 9 - epoch 1379 - loss: 2.1878
chain 9 - epoch 1380 - loss: 1.8985
chain 9 - epoch 1381 - loss: 4.1236
chain 9 - epoch 1382 - loss: 2.0357
chain 9 - epoch 1383 - loss: 2.2119
chain 9 - epoch 1384 - loss: 3.1994
chain 9 - epoch 1385 - loss:

chain 9 - epoch 1586 - loss: 2.7124
chain 9 - epoch 1587 - loss: 2.8137
chain 9 - epoch 1588 - loss: 3.2027
chain 9 - epoch 1589 - loss: 4.2423
chain 9 - epoch 1590 - loss: 2.4270
chain 9 - epoch 1591 - loss: 2.4219
chain 9 - epoch 1592 - loss: 4.5120
chain 9 - epoch 1593 - loss: 2.1727
chain 9 - epoch 1594 - loss: 1.8891
chain 9 - epoch 1595 - loss: 3.8268
chain 9 - epoch 1596 - loss: 1.9314
chain 9 - epoch 1597 - loss: 3.1583
chain 9 - epoch 1598 - loss: 2.9778
chain 9 - epoch 1599 - loss: 2.1691
chain 9 - epoch 1600 - loss: 2.8692
chain 9 - epoch 1601 - loss: 3.2331
chain 9 - epoch 1602 - loss: 2.8121
chain 9 - epoch 1603 - loss: 2.1913
chain 9 - epoch 1604 - loss: 2.5906
chain 9 - epoch 1605 - loss: 2.2334
chain 9 - epoch 1606 - loss: 3.4548
chain 9 - epoch 1607 - loss: 2.4097
chain 9 - epoch 1608 - loss: 3.1632
chain 9 - epoch 1609 - loss: 3.5985
chain 9 - epoch 1610 - loss: 1.7278
chain 9 - epoch 1611 - loss: 2.1078
chain 9 - epoch 1612 - loss: 3.3754
chain 9 - epoch 1613 - loss:

chain 9 - epoch 1814 - loss: 4.8311
chain 9 - epoch 1815 - loss: 2.8572
chain 9 - epoch 1816 - loss: 2.7597
chain 9 - epoch 1817 - loss: 2.0898
chain 9 - epoch 1818 - loss: 1.9327
chain 9 - epoch 1819 - loss: 2.1190
chain 9 - epoch 1820 - loss: 2.9052
chain 9 - epoch 1821 - loss: 1.9403
chain 9 - epoch 1822 - loss: 2.7960
chain 9 - epoch 1823 - loss: 3.0700
chain 9 - epoch 1824 - loss: 2.6204
chain 9 - epoch 1825 - loss: 5.1309
chain 9 - epoch 1826 - loss: 1.9535
chain 9 - epoch 1827 - loss: 2.3311
chain 9 - epoch 1828 - loss: 2.6503
chain 9 - epoch 1829 - loss: 2.1892
chain 9 - epoch 1830 - loss: 4.1289
chain 9 - epoch 1831 - loss: 3.1916
chain 9 - epoch 1832 - loss: 3.4876
chain 9 - epoch 1833 - loss: 3.4129
chain 9 - epoch 1834 - loss: 2.8577
chain 9 - epoch 1835 - loss: 2.4405
chain 9 - epoch 1836 - loss: 2.7024
chain 9 - epoch 1837 - loss: 6.0232
chain 9 - epoch 1838 - loss: 4.1725
chain 9 - epoch 1839 - loss: 2.1088
chain 9 - epoch 1840 - loss: 3.8872
chain 9 - epoch 1841 - loss:

chain 9 - epoch 2043 - loss: 2.8787
chain 9 - epoch 2044 - loss: 5.5526
chain 9 - epoch 2045 - loss: 3.0260
chain 9 - epoch 2046 - loss: 2.3248
chain 9 - epoch 2047 - loss: 3.4473
chain 9 - epoch 2048 - loss: 3.8191
chain 9 - epoch 2049 - loss: 1.9713
chain 9 - epoch 2050 - loss: 2.0087
chain 9 - epoch 2051 - loss: 2.4273
chain 9 - epoch 2052 - loss: 4.6890
chain 9 - epoch 2053 - loss: 2.6556
chain 9 - epoch 2054 - loss: 3.7546
chain 9 - epoch 2055 - loss: 3.4999
chain 9 - epoch 2056 - loss: 2.9301
chain 9 - epoch 2057 - loss: 3.3590
chain 9 - epoch 2058 - loss: 2.7523
chain 9 - epoch 2059 - loss: 1.7950
chain 9 - epoch 2060 - loss: 3.2993
chain 9 - epoch 2061 - loss: 2.0208
chain 9 - epoch 2062 - loss: 2.0479
chain 9 - epoch 2063 - loss: 3.9584
chain 9 - epoch 2064 - loss: 2.6436
chain 9 - epoch 2065 - loss: 2.5998
chain 9 - epoch 2066 - loss: 3.2305
chain 9 - epoch 2067 - loss: 2.5694
chain 9 - epoch 2068 - loss: 2.5682
chain 9 - epoch 2069 - loss: 2.5766
chain 9 - epoch 2070 - loss:

chain 9 - epoch 2272 - loss: 2.1220
chain 9 - epoch 2273 - loss: 3.3829
chain 9 - epoch 2274 - loss: 1.9235
chain 9 - epoch 2275 - loss: 2.3021
chain 9 - epoch 2276 - loss: 2.3910
chain 9 - epoch 2277 - loss: 2.9119
chain 9 - epoch 2278 - loss: 4.1366
chain 9 - epoch 2279 - loss: 3.0596
chain 9 - epoch 2280 - loss: 1.8949
chain 9 - epoch 2281 - loss: 3.1541
chain 9 - epoch 2282 - loss: 2.6424
chain 9 - epoch 2283 - loss: 2.2579
chain 9 - epoch 2284 - loss: 2.7442
chain 9 - epoch 2285 - loss: 2.1156
chain 9 - epoch 2286 - loss: 2.5966
chain 9 - epoch 2287 - loss: 3.8000
chain 9 - epoch 2288 - loss: 2.1384
chain 9 - epoch 2289 - loss: 2.3126
chain 9 - epoch 2290 - loss: 2.9973
chain 9 - epoch 2291 - loss: 2.4159
chain 9 - epoch 2292 - loss: 3.4468
chain 9 - epoch 2293 - loss: 2.0645
chain 9 - epoch 2294 - loss: 3.5773
chain 9 - epoch 2295 - loss: 2.3787
chain 9 - epoch 2296 - loss: 2.9915
chain 9 - epoch 2297 - loss: 2.9338
chain 9 - epoch 2298 - loss: 2.2734
chain 9 - epoch 2299 - loss:

In [46]:
np.save(ll_psgld_boston, ll_psgld)
np.save(rmse_psgld_boston, rmse_psgld)
np.save(predictions_psgld_boston, predictions)

tensor(-2.3406)

In [47]:
gelman_rubin(predictions)

tensor(1.0136)

In [ ]:
ess(predictions[:,1:])

### avg. Test log-likelihood

In [12]:
ll_mean = np.mean(ll_ksgfs[:,-1])
ll_std = np.std(ll_ksgfs[:,-1])
print(ll_mean, ll_std)

-2.3240952491760254 0.03602292913042259


### avg. Test RMSE

In [13]:
rmse_mean = np.mean(rmse_ksgfs[:,-1])
rmse_std = np.std(rmse_ksgfs[:,-1])
print(rmse_mean, rmse_std)

## K-SGLD

In [6]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgld



np.random.seed(42)
torch.manual_seed(42)
    
lr = 5e-4
l2 = 1e-3
lambda_ = 1.
eta = 1.
v = 0

batch_size = 32
dataset_size=456

n_chains = 10
n_samples = 300


ll_ksgld = np.zeros((n_chains, n_samples))
rmse_ksgld = np.zeros((n_chains, n_samples))






losses_ksgld = []
for i in range(n_chains):
    network = Model()
    criterion = nn.MSELoss(size_average=False)
    #eps=5e-2

    optim = ksgld.optim.KSGLD(network, criterion, batch_size, dataset_size, eta=eta., v=v., lambda_=lambda_, epsilon=lr, l2=l2, invert_every=1)
    evaluate = evaluation(test_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

    t = 1.
    n = 0
    

    for epoch in range(2500):
        running_loss = 0
        for x, y in iter(train_loader):
            x = x.view(x.size(0), -1)

            optim.update_curvature(x)

            network.zero_grad()
            output = network(x)
            loss = 0.5 * criterion(output, y)
            loss.backward()
            optim.step()

            running_loss += loss * batch_size / dataset_size

            if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                rmse, ll, predictions = evaluate.fn(network)

                ll_ksgld[i, n] = ll
                rmse_ksgld[i, n] = rmse

                n += 1

            t += 1.


        print("chain {:d} - epoch {:d} - loss: {:.4f} ".format(i, epoch, running_loss))

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 0 - loss: 16.6652 
chain 0 - epoch 1 - loss: 16.2222 
chain 0 - epoch 2 - loss: 17.0376 
chain 0 - epoch 3 - loss: 16.3490 
chain 0 - epoch 4 - loss: 15.1785 
chain 0 - epoch 5 - loss: 15.6027 
chain 0 - epoch 6 - loss: 16.7416 
chain 0 - epoch 7 - loss: 18.1121 
chain 0 - epoch 8 - loss: 18.6324 
chain 0 - epoch 9 - loss: 18.1973 
chain 0 - epoch 10 - loss: 16.5866 
chain 0 - epoch 11 - loss: 16.3043 
chain 0 - epoch 12 - loss: 14.1198 
chain 0 - epoch 13 - loss: 13.3338 
chain 0 - epoch 14 - loss: 12.1864 
chain 0 - epoch 15 - loss: 12.4095 
chain 0 - epoch 16 - loss: 12.4419 
chain 0 - epoch 17 - loss: 12.3960 
chain 0 - epoch 18 - loss: 12.9712 


/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


chain 0 - epoch 19 - loss: 13.1436 
chain 0 - epoch 20 - loss: 13.2235 
chain 0 - epoch 21 - loss: 13.4995 
chain 0 - epoch 22 - loss: 13.3721 
chain 0 - epoch 23 - loss: 13.9025 
chain 0 - epoch 24 - loss: 14.6453 
chain 0 - epoch 25 - loss: 15.9387 
chain 0 - epoch 26 - loss: 13.3298 
chain 0 - epoch 27 - loss: 13.2443 
chain 0 - epoch 28 - loss: 12.7121 
chain 0 - epoch 29 - loss: 11.8134 
chain 0 - epoch 30 - loss: 11.4589 
chain 0 - epoch 31 - loss: 11.9498 
chain 0 - epoch 32 - loss: 12.3799 
chain 0 - epoch 33 - loss: 12.6080 
chain 0 - epoch 34 - loss: 13.2675 
chain 0 - epoch 35 - loss: 12.4192 
chain 0 - epoch 36 - loss: 10.9913 
chain 0 - epoch 37 - loss: 9.5152 
chain 0 - epoch 38 - loss: 9.3943 
chain 0 - epoch 39 - loss: 8.6339 
chain 0 - epoch 40 - loss: 8.3571 
chain 0 - epoch 41 - loss: 8.2759 
chain 0 - epoch 42 - loss: 8.0122 
chain 0 - epoch 43 - loss: 7.9642 
chain 0 - epoch 44 - loss: 7.5515 
chain 0 - epoch 45 - loss: 7.9612 
chain 0 - epoch 46 - loss: 7.9612 
ch

chain 0 - epoch 250 - loss: 5.4448 
chain 0 - epoch 251 - loss: 5.7741 
chain 0 - epoch 252 - loss: 6.3464 
chain 0 - epoch 253 - loss: 6.2035 
chain 0 - epoch 254 - loss: 6.3842 
chain 0 - epoch 255 - loss: 6.8694 
chain 0 - epoch 256 - loss: 7.1847 
chain 0 - epoch 257 - loss: 7.4583 
chain 0 - epoch 258 - loss: 9.2027 
chain 0 - epoch 259 - loss: 9.9454 
chain 0 - epoch 260 - loss: 9.4111 
chain 0 - epoch 261 - loss: 9.3860 
chain 0 - epoch 262 - loss: 8.6278 
chain 0 - epoch 263 - loss: 8.3209 
chain 0 - epoch 264 - loss: 7.4913 
chain 0 - epoch 265 - loss: 6.7899 
chain 0 - epoch 266 - loss: 6.7329 
chain 0 - epoch 267 - loss: 7.7098 
chain 0 - epoch 268 - loss: 8.7569 
chain 0 - epoch 269 - loss: 8.5332 
chain 0 - epoch 270 - loss: 8.3550 
chain 0 - epoch 271 - loss: 8.0243 
chain 0 - epoch 272 - loss: 7.9625 
chain 0 - epoch 273 - loss: 8.0083 
chain 0 - epoch 274 - loss: 9.0819 
chain 0 - epoch 275 - loss: 9.9071 
chain 0 - epoch 276 - loss: 9.3866 
chain 0 - epoch 277 - loss: 

...

chain 9 - epoch 1482 - loss: 5.6176 
chain 9 - epoch 1483 - loss: 5.8683 
chain 9 - epoch 1484 - loss: 6.0117 
chain 9 - epoch 1485 - loss: 5.9900 
chain 9 - epoch 1486 - loss: 6.5934 
chain 9 - epoch 1487 - loss: 6.8675 
chain 9 - epoch 1488 - loss: 6.6466 
chain 9 - epoch 1489 - loss: 5.9719 
chain 9 - epoch 1490 - loss: 6.2956 
chain 9 - epoch 1491 - loss: 6.3517 
chain 9 - epoch 1492 - loss: 6.1230 
chain 9 - epoch 1493 - loss: 6.5788 
chain 9 - epoch 1494 - loss: 7.7053 
chain 9 - epoch 1495 - loss: 7.6266 
chain 9 - epoch 1496 - loss: 8.2321 
chain 9 - epoch 1497 - loss: 7.9165 
chain 9 - epoch 1498 - loss: 7.6049 
chain 9 - epoch 1499 - loss: 7.1544 
chain 9 - epoch 1500 - loss: 7.5115 
chain 9 - epoch 1501 - loss: 7.4681 
chain 9 - epoch 1502 - loss: 6.7583 
chain 9 - epoch 1503 - loss: 6.1428 
chain 9 - epoch 1504 - loss: 6.3027 
chain 9 - epoch 1505 - loss: 5.9688 
chain 9 - epoch 1506 - loss: 6.1943 
chain 9 - epoch 1507 - loss: 6.2741 
chain 9 - epoch 1508 - loss: 6.2321 
c

chain 9 - epoch 1704 - loss: 5.3168 
chain 9 - epoch 1705 - loss: 5.2469 
chain 9 - epoch 1706 - loss: 5.3287 
chain 9 - epoch 1707 - loss: 4.9783 
chain 9 - epoch 1708 - loss: 4.8820 
chain 9 - epoch 1709 - loss: 4.8440 
chain 9 - epoch 1710 - loss: 5.4849 
chain 9 - epoch 1711 - loss: 5.2088 
chain 9 - epoch 1712 - loss: 4.9049 
chain 9 - epoch 1713 - loss: 4.8129 
chain 9 - epoch 1714 - loss: 4.4464 
chain 9 - epoch 1715 - loss: 4.5040 
chain 9 - epoch 1716 - loss: 4.4936 
chain 9 - epoch 1717 - loss: 4.6524 
chain 9 - epoch 1718 - loss: 4.6705 
chain 9 - epoch 1719 - loss: 4.9887 
chain 9 - epoch 1720 - loss: 5.4585 
chain 9 - epoch 1721 - loss: 5.4311 
chain 9 - epoch 1722 - loss: 4.8151 
chain 9 - epoch 1723 - loss: 4.9288 
chain 9 - epoch 1724 - loss: 4.4934 
chain 9 - epoch 1725 - loss: 4.5620 
chain 9 - epoch 1726 - loss: 4.4008 
chain 9 - epoch 1727 - loss: 4.3444 
chain 9 - epoch 1728 - loss: 4.3450 
chain 9 - epoch 1729 - loss: 4.1495 
chain 9 - epoch 1730 - loss: 4.0774 
c

chain 9 - epoch 1927 - loss: 5.7177 
chain 9 - epoch 1928 - loss: 6.7638 
chain 9 - epoch 1929 - loss: 7.3894 
chain 9 - epoch 1930 - loss: 6.6443 
chain 9 - epoch 1931 - loss: 6.1088 
chain 9 - epoch 1932 - loss: 7.1359 
chain 9 - epoch 1933 - loss: 7.9355 
chain 9 - epoch 1934 - loss: 7.9146 
chain 9 - epoch 1935 - loss: 6.8902 
chain 9 - epoch 1936 - loss: 6.4130 
chain 9 - epoch 1937 - loss: 5.5230 
chain 9 - epoch 1938 - loss: 5.8282 
chain 9 - epoch 1939 - loss: 4.9864 
chain 9 - epoch 1940 - loss: 4.9630 
chain 9 - epoch 1941 - loss: 5.3008 
chain 9 - epoch 1942 - loss: 5.2446 
chain 9 - epoch 1943 - loss: 4.4774 
chain 9 - epoch 1944 - loss: 4.5807 
chain 9 - epoch 1945 - loss: 5.4293 
chain 9 - epoch 1946 - loss: 6.5985 
chain 9 - epoch 1947 - loss: 5.2176 
chain 9 - epoch 1948 - loss: 4.6343 
chain 9 - epoch 1949 - loss: 4.5219 
chain 9 - epoch 1950 - loss: 6.0838 
chain 9 - epoch 1951 - loss: 5.4455 
chain 9 - epoch 1952 - loss: 5.2250 
chain 9 - epoch 1953 - loss: 7.6448 
c

chain 9 - epoch 2148 - loss: 3.8488 
chain 9 - epoch 2149 - loss: 3.9043 
chain 9 - epoch 2150 - loss: 4.1600 
chain 9 - epoch 2151 - loss: 4.7983 
chain 9 - epoch 2152 - loss: 6.2556 
chain 9 - epoch 2153 - loss: 6.7333 
chain 9 - epoch 2154 - loss: 6.6105 
chain 9 - epoch 2155 - loss: 6.2819 
chain 9 - epoch 2156 - loss: 5.2914 
chain 9 - epoch 2157 - loss: 4.9115 
chain 9 - epoch 2158 - loss: 5.6621 
chain 9 - epoch 2159 - loss: 5.9223 
chain 9 - epoch 2160 - loss: 5.3151 
chain 9 - epoch 2161 - loss: 5.2176 
chain 9 - epoch 2162 - loss: 5.4626 
chain 9 - epoch 2163 - loss: 5.0464 
chain 9 - epoch 2164 - loss: 5.2281 
chain 9 - epoch 2165 - loss: 5.9619 
chain 9 - epoch 2166 - loss: 6.0741 
chain 9 - epoch 2167 - loss: 5.8808 
chain 9 - epoch 2168 - loss: 7.0145 
chain 9 - epoch 2169 - loss: 7.0852 
chain 9 - epoch 2170 - loss: 7.9163 
chain 9 - epoch 2171 - loss: 7.6282 
chain 9 - epoch 2172 - loss: 6.2274 
chain 9 - epoch 2173 - loss: 6.0747 
chain 9 - epoch 2174 - loss: 5.4438 
c

chain 9 - epoch 2369 - loss: 7.6173 
chain 9 - epoch 2370 - loss: 8.9510 
chain 9 - epoch 2371 - loss: 9.7474 
chain 9 - epoch 2372 - loss: 7.2748 
chain 9 - epoch 2373 - loss: 7.0033 
chain 9 - epoch 2374 - loss: 6.7352 
chain 9 - epoch 2375 - loss: 6.3839 
chain 9 - epoch 2376 - loss: 5.2040 
chain 9 - epoch 2377 - loss: 4.7627 
chain 9 - epoch 2378 - loss: 4.7196 
chain 9 - epoch 2379 - loss: 5.4371 
chain 9 - epoch 2380 - loss: 5.8255 
chain 9 - epoch 2381 - loss: 6.1636 
chain 9 - epoch 2382 - loss: 6.6409 
chain 9 - epoch 2383 - loss: 6.2157 
chain 9 - epoch 2384 - loss: 5.7795 
chain 9 - epoch 2385 - loss: 5.1537 
chain 9 - epoch 2386 - loss: 4.3930 
chain 9 - epoch 2387 - loss: 4.1426 
chain 9 - epoch 2388 - loss: 4.7527 
chain 9 - epoch 2389 - loss: 4.8661 
chain 9 - epoch 2390 - loss: 4.8520 
chain 9 - epoch 2391 - loss: 4.6397 
chain 9 - epoch 2392 - loss: 4.9706 
chain 9 - epoch 2393 - loss: 5.5550 
chain 9 - epoch 2394 - loss: 6.0995 
chain 9 - epoch 2395 - loss: 6.0795 
c

### avg. Test log-likelihood

In [7]:
ll_mean = np.mean(ll_ksgld[:,-1])
ll_std = np.std(ll_ksgld[:,-1])
print(ll_mean, ll_std)

-3.0486520767211913 0.21127632086697642


### avg. Test RMSE

In [8]:
rmse_mean = np.mean(rmse_ksgld[:,-1])
rmse_std = np.std(rmse_ksgld[:,-1])
print(rmse_mean, rmse_std)

## Plot Test log-likelihoods and RMSE

### Test log-likelihood

In [ ]:
# Compute running avg. test log-likelihood and std. error 
ll_meanRunningSGLD = np.mean(ll_sgld, 0)
ll_stdRunningSGLD = np.std(ll_sgld, 0)
ll_upperSGLD = ll_meanRunningSGLD + ll_stdRunningSGLD
ll_lowerSGLD = ll_meanRunningSGLD - ll_stdRunningSGLD

ll_meanRunningPSGLD = np.mean(ll_psgld, 0)
ll_stdRunningPSGLD = np.std(ll_psgld, 0)
ll_upperPSGLD = ll_meanRunningPSGDL + ll_stdRunningPSGLD
ll_lowerPSGLD = ll_meanRunningPSGLD - ll_stdRunningPSGLD

ll_meanRunningKSGLD = np.mean(ll_ksgld, 0)
ll_stdRunningKSGLD = np.std(ll_ksgld, 0)
ll_upperKSGLD = ll_meanRunningKSGDL + ll_stdRunningKSGLD
ll_lowerKSGLD = ll_meanRunningKSGLD - ll_stdRunningKSGLD

ll_meanRunningKSGFS = np.mean(ll_ksgfs, 0)
ll_stdRunningKSGFS = np.std(ll_ksgfs, 0)
ll_upperKSGFS = ll_meanRunningKSGFS + ll_stdRunningKSGFS
ll_lowerKSGFS = ll_meanRunningKSGFS - ll_stdRunningKSGFS

In [ ]:
plt.figure(figsize=(21,9))

plt.plot(range(n_samples),ll_meanRunningSGLD)
plt.plot(range(n_samples),ll_meanRunningPSGLD)
plt.plot(range(n_samples),ll_meanRunningKSGLD)
plt.plot(range(n_samples),ll_meanRunningKSGFS)

plt.plot(range(n_samples),ll_upperSGLD,'blue',alpha=0.15)
plt.plot(range(n_samples),ll_lowerSGLD,'blue', alpha=0.15)
plt.plot(range(n_samples),ll_upperPSGLD,'red',alpha=0.15)
plt.plot(range(n_samples),ll_lowerPSGLD,'red', alpha=0.15)
plt.plot(range(n_samples),ll_upperKSGLD,'orange',alpha=0.15)
plt.plot(range(n_samples),ll_lowerKSGLD,'orange', alpha=0.15)
plt.plot(range(n_samples),ll_upperKSGFS,'green',alpha=0.15)
plt.plot(range(n_samples),ll_lowerKSGFS,'green', alpha=0.15)

plt.fill_between(range(n_samples),ll_lowerSGLD, ll_upperSGLD, facecolor='blue', alpha=0.15, interpolate=True)
plt.fill_between(range(n_samples),ll_lowerPSGLD, ll_upperPSGLD, facecolor='red', alpha=0.15, interpolate=True)
plt.fill_between(range(n_samples),ll_lowerKSGLD, ll_upperKSGLD, facecolor='orange', alpha=0.15, interpolate=True)
plt.fill_between(range(n_samples),ll_lowerKSGFS, ll_upperKSGFS, facecolor='green', alpha=0.15, interpolate=True)

plt.xlabel("Number of Samples")
plt.ylabel("Test Log-Likelihood")
plt.ylim(-4,0)

### RMSE

In [ ]:
rmse_meanRunningSGLD = np.mean(rmse_sgld, 0)
rmse_stdRunningSGLD = np.std(rmse_sgld, 0)
rmse_upperSGLD = rmse_meanRunningSGLD + rmse_stdRunningSGLD
rmse_lowerSGLD = rmse_meanRunningSGLD - rmse_stdRunningSGLD

rmse_meanRunningPSGLD = np.mean(rmse_psgld, 0)
rmse_stdRunningPSGLD = np.std(rmse_psgld, 0)
rmse_upperPSGLD = rmse_meanRunningPSGLD + rmse_stdRunningPSGLD
rmse_lowerPSGLD = rmse_meanRunningPSGLD - rmse_stdRunningPSGLD

rmse_meanRunningKSGLD = np.mean(rmse_ksgld, 0)
rmse_stdRunningKSGLD = np.std(rmse_ksgld, 0)
rmse_upperKSGLD = rmse_meanRunningKSGLD + rmse_stdRunningKSGLD
rmse_lowerKSGLD = rmse_meanRunningKSGLD - rmse_stdRunningKSGLD

rmse_meanRunningKSGFS = np.mean(rmse_ksgfs, 0)
rmse_stdRunningKSGFS = np.std(rmse_ksgfs, 0)
rmse_upperKSGFS = rmse_meanRunningKSGFS + rmse_stdRunningKSGFS
rmse_lowerKSGFS = rmse_meanRunningKSGFS - rmse_stdRunningKSGFS

In [ ]:
plt.figure(figsize=(21,9))

plt.plot(n_samples,rmse_meanRunningSGLD)
plt.plot(n_samples,rmse_meanRunningPSGLD)
plt.plot(n_samples,rmse_meanRunningKSGLD)
plt.plot(n_samples,rmse_meanRunningKSGFS)

plt.plot(range(n_samples),rmse_upperSGLD,'blue',alpha=0.15)
plt.plot(range(n_samples),rmse_lowerSGLD,'blue', alpha=0.15)
plt.plot(range(n_samples),rmse_upperPSGLD,'red',alpha=0.15)
plt.plot(range(n_samples),rmse_lowerPSGLD,'red', alpha=0.15)
plt.plot(range(n_samples),rmse_upperKSGLD,'orange',alpha=0.15)
plt.plot(range(n_samples),rmse_lowerKSGLD,'orange', alpha=0.15)
plt.plot(range(n_samples),rmse_upperKSGFS,'green',alpha=0.15)
plt.plot(range(n_samples),rmse_lowerKSGFS,'green', alpha=0.15)

plt.fill_between(range(n_samples),rmse_lowerSGLD, rmse_upperSGLD, facecolor='blue', alpha=0.15, interpolate=True)
plt.fill_between(range(n_samples),rmse_lowerPSGLD, rmse_upperPSGLD, facecolor='red', alpha=0.15, interpolate=True)
plt.fill_between(range(n_samples),rmse_lowerKSGLD, rmse_upperKSGLD, facecolor='orange', alpha=0.15, interpolate=True)
plt.fill_between(range(n_samples),rmse_lowerKSGFS, rmse_upperKSGFS, facecolor='green', alpha=0.15, interpolate=True)

plt.xlabel("Number of Samples")
plt.ylabel("RMSE")
